In [2]:
import mpl_toolkits
import matplotlib.pyplot as plt
import pandas as pd
import geopandas as gpd
import numpy as np
import pickle
import os
import logging
from obspy import read


from obspy.clients.fdsn.mass_downloader import RectangularDomain, Restrictions, MassDownloader
from scipy import signal
from obspy import UTCDateTime
from obspy.clients.fdsn import Client as FDSN_Client
from obspy import read_inventory
from obspy.core.util import (BASEMAP_VERSION, CARTOPY_VERSION,
                             MATPLOTLIB_VERSION, PROJ4_VERSION)

In [3]:
events_df = pd.read_pickle('data/events_processed.pkl')
stations_df = pd.read_pickle('data/stations_processed.pkl')

In [4]:
events = events_df[(events_df.time > '2020-01-01') & (events_df.time < '2021-01-01')]

In [5]:
events.shape

(15825, 6)

In [6]:
events.head()
events.tail()

event_id                         time   latitude  \
18432  smi:nz.org.geonet/2020p983077  2020-12-29T17:43:53.875978Z -44.475433   
18433  smi:nz.org.geonet/2020p983836  2020-12-30T00:27:16.898049Z -36.774952   
18434  smi:nz.org.geonet/2020p984504  2020-12-30T06:24:11.460502Z -39.237202   
18435  smi:nz.org.geonet/2020p985078  2020-12-30T11:29:47.004685Z -41.701187   
18439  smi:nz.org.geonet/2020p986263  2020-12-30T22:01:10.265479Z -40.155788   

        longitude  magnitude         depth  
18432  168.628998   2.613268    5000.00000  
18433  177.550446   2.650505  185424.91150  
18434  174.652115   2.374883  153993.97280  
18435  177.772430   2.804164   12000.00000  
18439  174.970612   2.721440   11283.76389

In [7]:
events = events[200:500]

In [ ]:
events.shape

In [8]:
def mass_data_downloader(start, stop, event_id, Station,
                         Network='NZ', 
                         Channel='HHZ', 
                         Location=10
                         ):
    '''
    This function uses the FDSN mass data downloader to automatically download
    data from the XH network deployed on the RIS from Nov 2014 - Nov 2016.
    More information on the Obspy mass downloader available at:
    https://docs.obspy.org/packages/autogen/obspy.clients.fdsn.mass_downloader.html
    Inputs:
    start: "YYYYMMDD"
    stop:  "YYYYMMDD"
    Network: 2-character FDSN network code
    Station: 2-character station code
    Channel: 3-character channel code
    Location: 10.
    '''
    print("=" * 65)
    print("Initiating mass download request.")

    domain = RectangularDomain(
        minlatitude=-47.749,
        maxlatitude=-33.779,
        minlongitude=166.104,
        maxlongitude=178.990
    )

    restrictions = Restrictions(
        starttime = start,
        endtime = stop,
        #24 hr
        chunklength_in_sec = 86400,
        network = Network,
        station = Station,
        location = Location,
        channel = Channel,
        reject_channels_with_gaps = False,
        minimum_length = 0.0,
        minimum_interstation_distance_in_m = 100.0
    )

    mdl = MassDownloader(providers=['GEONET'])
    mdl.download(
        domain,
        restrictions,
        mseed_storage=f"normal/waveforms/{event_id}",
        stationxml_storage="normal/stations"
    )

    logger = logging.getLogger("obspy.clients.fdsn.mass_downloader")
    logger.setLevel(logging.DEBUG)

In [ ]:
for i, event in events.iterrows():
    event_id = event.event_id
    
    for j, station in stations_df.iterrows():
        event_time = event['time']
        
        start=event_time - 3000
        end=event_time - 2970
        mass_data_downloader(start, end, event_id, station.station_code)

[2021-11-25 00:39:36,140] - obspy.clients.fdsn.mass_downloader - INFO: Initializing FDSN client(s) for GEONET.


Initiating mass download request.


[2021-11-25 00:39:38,579] - obspy.clients.fdsn.mass_downloader - INFO: Successfully initialized 1 client(s): GEONET.
[2021-11-25 00:39:38,588] - obspy.clients.fdsn.mass_downloader - INFO: Total acquired or preexisting stations: 0
[2021-11-25 00:39:38,589] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Requesting unreliable availability.
[2021-11-25 00:39:39,260] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Successfully requested availability (0.67 seconds)
[2021-11-25 00:39:39,262] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Found 1 stations (1 channels).
[2021-11-25 00:39:39,263] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Will attempt to download data from 1 stations.
[2021-11-25 00:39:39,264] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Status for 1 time intervals/channels before downloading: NEEDS_DOWNLOADING
[2021-11-25 00:39:40,473] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET

Initiating mass download request.


[2021-11-25 00:39:41,086] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Successfully requested availability (0.57 seconds)
[2021-11-25 00:39:41,086] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Found 1 stations (1 channels).
[2021-11-25 00:39:41,087] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Will attempt to download data from 1 stations.
[2021-11-25 00:39:41,087] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Status for 1 time intervals/channels before downloading: NEEDS_DOWNLOADING
[2021-11-25 00:39:43,001] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Successfully downloaded 1 channels (of 1)
[2021-11-25 00:39:43,009] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Launching basic QC checks...
[2021-11-25 00:39:43,023] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Downloaded 0.0 MB [2.08 KB/sec] of data, 0.0 MB of which were discarded afterwards.
[2021-11-25 00:39:

...

[2021-11-25 02:17:22,729] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Successfully requested availability (0.65 seconds)
[2021-11-25 02:17:22,748] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Found 1 stations (1 channels).
[2021-11-25 02:17:22,752] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Will attempt to download data from 1 stations.
[2021-11-25 02:17:22,756] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Status for 1 time intervals/channels before downloading: NEEDS_DOWNLOADING
[2021-11-25 02:17:23,576] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Successfully downloaded 1 channels (of 1)
[2021-11-25 02:17:23,638] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Launching basic QC checks...
[2021-11-25 02:17:23,741] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Downloaded 0.0 MB [5.24 KB/sec] of data, 0.0 MB of which were discarded afterwards.
[2021-11-25 02:17:

Initiating mass download request.


[2021-11-25 02:17:24,578] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Successfully requested availability (0.75 seconds)
[2021-11-25 02:17:24,620] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Found 1 stations (1 channels).
[2021-11-25 02:17:24,627] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Will attempt to download data from 1 stations.
[2021-11-25 02:17:24,658] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Status for 1 time intervals/channels before downloading: NEEDS_DOWNLOADING
[2021-11-25 02:17:25,810] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Successfully downloaded 1 channels (of 1)
[2021-11-25 02:17:25,950] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Launching basic QC checks...
[2021-11-25 02:17:25,989] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Downloaded 0.0 MB [3.25 KB/sec] of data, 0.0 MB of which were discarded afterwards.
[2021-11-25 02:17:

Initiating mass download request.


[2021-11-25 02:17:26,850] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Successfully requested availability (0.62 seconds)
[2021-11-25 02:17:26,964] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Found 1 stations (1 channels).
[2021-11-25 02:17:26,985] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Will attempt to download data from 1 stations.
[2021-11-25 02:17:26,991] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Status for 1 time intervals/channels before downloading: NEEDS_DOWNLOADING
[2021-11-25 02:17:27,995] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Successfully downloaded 1 channels (of 1)
[2021-11-25 02:17:28,050] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Launching basic QC checks...
[2021-11-25 02:17:28,118] - obspy.clients.fdsn.mass_downloader - INFO: Client 'GEONET' - Downloaded 0.0 MB [3.40 KB/sec] of data, 0.0 MB of which were discarded afterwards.
[2021-11-25 02:17: